In [1]:
import torch
import pickle
import numpy as np
from argparse import Namespace
from torch.utils.data import DataLoader
import torch.nn.functional as F
from heterogt.utils.tokenizer import EHRTokenizer
from heterogt.utils.dataset import FineTuneEHRDataset, batcher, expand_level3
from heterogt.utils.train import train_with_early_stopping, PHENO_ORDER
from heterogt.utils.seed import set_random_seed
from heterogt.model.model import HeteroGTFineTune

Disabling PyTorch because PyTorch >= 2.1 is required but found 1.13.1
None of PyTorch, TensorFlow >= 2.0, or Flax have been found. Models won't be available and only tokenizers, configuration and file/data utilities can be used.


In [2]:
set_random_seed(123)

[INFO] Random seed set to 123


In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [4]:
config = Namespace(
    dataset = "MIMIC-III",
    tasks = ["death", "readmission", "stay", "next_diag_6m", "next_diag_12m"],
    task_index = 3,  # index of the task to train
    token_type = ["diag", "med", "lab", "pro"],
    special_tokens = ["[PAD]", "[CLS]"],
    # only for tf layer
    attn_mask_dicts = [{1:[6,7], 2:[6,7], 3:[6,7], 4:[6,7], 5:[6,7], 6:[1,2,3,4,5,6,7], 7:[1,2,3,4,5,6,7]}, 
                       {1:[6,7], 2:[6,7], 3:[6,7], 4:[6,7], 5:[6,7], 6:[1,2,3,4,5,6,7], 7:[1,2,3,4,5,6,7]}], 
    d_model = 64,
    num_heads = 4,
    batch_size = 32,
    lr = 1e-3,
    epochs = 500,
    early_stop_patience = 5,
    group_code_thre = 5,  # if there are group_code_thre diag codes belongs to the same group ICD code, then the group code is generated
    use_pretrained_model = True,
    pretrain_mask_rate = 0.7,
    pretrain_cls_ontology_weight = 5e-2,
    pretrain_visit_ontology_weight = 5e-2,
    pretrain_adm_type_weight = 0,
    dec_loss_lambda = 1e-2,
)

In [5]:
full_data_path = f"./data_process/{config.dataset}-processed/mimic.pkl"  # for tokenizer
curr_task = config.tasks[config.task_index]
print("Current task:", curr_task)
if curr_task == "next_diag_6m":
    finetune_data_path = f"./data_process/{config.dataset}-processed/mimic_nextdiag_6m.pkl"
elif curr_task == "next_diag_12m":
    finetune_data_path = f"./data_process/{config.dataset}-processed/mimic_nextdiag_12m.pkl"
else:
    finetune_data_path = f"./data_process/{config.dataset}-processed/mimic_downstream.pkl"

Current task: next_diag_6m


In [6]:
ehr_full_data = pickle.load(open(full_data_path, 'rb'))
group_code_sentences = [expand_level3()[1]]
diag_sentences = ehr_full_data["ICD9_CODE"].values.tolist()
med_sentences = ehr_full_data["NDC"].values.tolist()
lab_sentences = ehr_full_data["LAB_TEST"].values.tolist()
pro_sentences = ehr_full_data["PRO_CODE"].values.tolist()
age_sentences = [[str(c)] for c in set(ehr_full_data["AGE"].values.tolist())] # important of [[]]
adm_type_sentences = ehr_full_data["ADMISSION_TYPE"].values.tolist()
max_admissions = ehr_full_data.groupby("SUBJECT_ID")["HADM_ID"].nunique().max()
config.max_num_adms = max_admissions
print(f"Max admissions per patient: {config.max_num_adms}")

Max admissions per patient: 8


In [7]:
tokenizer = EHRTokenizer(age_sentences, group_code_sentences, diag_sentences, med_sentences, lab_sentences, 
                         pro_sentences, special_tokens=config.special_tokens, adm_types_sentences=adm_type_sentences)
config.label_vocab_size = len(PHENO_ORDER)  # a set of predifined diseases
config.global_vocab_size = len(tokenizer.vocab.id2word)
config.age_vocab_size = tokenizer.token_number("age")
config.group_code_vocab_size = tokenizer.token_number("group")
print(f"Age vocabulary size: {config.age_vocab_size}")
print(f"Group code vocabulary size: {config.group_code_vocab_size}")

Age vocabulary size: 18
Group code vocabulary size: 19


In [8]:
train_data, val_data, test_data = pickle.load(open(finetune_data_path, 'rb'))
# example label percentage
print("Percentage of DEATH in test dataset:",
      (test_data["DEATH"] == True).mean() * 100, "%")

print("Percentage of READMISSION in test dataset:",
      (test_data["READMISSION"] == 1).mean() * 100, "%")

print("Percentage of STAY>7 days in test dataset:",
      (test_data["STAY_DAYS"] > 7).mean() * 100, "%")

Percentage of DEATH in test dataset: 7.858376511226252 %
Percentage of READMISSION in test dataset: 65.24179620034542 %
Percentage of STAY>7 days in test dataset: 55.44041450777202 %


In [9]:
train_dataset = FineTuneEHRDataset(train_data, tokenizer, token_type=config.token_type, task=curr_task, 
                                   max_num_adms=config.max_num_adms, group_code_thre=config.group_code_thre)
val_dataset = FineTuneEHRDataset(val_data, tokenizer, token_type=config.token_type, task=curr_task, 
                                 max_num_adms=config.max_num_adms, group_code_thre=config.group_code_thre)
test_dataset = FineTuneEHRDataset(test_data, tokenizer, token_type=config.token_type, task=curr_task, 
                                   max_num_adms=config.max_num_adms, group_code_thre=config.group_code_thre)

In [10]:
long_adm_seq_crite = 3
val_long_seq_idx, test_long_seq_idx = [], []
for i in range(len(val_dataset)):
    hadm_id = list(val_dataset.records.keys())[i]
    num_adms = len(val_dataset.records[hadm_id])
    if num_adms >= long_adm_seq_crite:
        val_long_seq_idx.append(i)
for i in range(len(test_dataset)):
    hadm_id = list(test_dataset.records.keys())[i]
    num_adms = len(test_dataset.records[hadm_id])
    if num_adms >= long_adm_seq_crite:
        test_long_seq_idx.append(i)
print(len(val_long_seq_idx), len(test_long_seq_idx))

151 168


In [11]:
num_group_code = []
for i in range(len(train_dataset)):
    input_ids, token_types, adm_index, age_ids, diag_group_codes, labels = train_dataset[i]
    count = (token_types[0] == 6).sum().item()
    num_group_code.append(count)
print("Mean group token numer per patient", np.mean(num_group_code))

Mean group token numer per patient 0.8702239789196311


In [12]:
train_dataloader = DataLoader(
    train_dataset,
    collate_fn=batcher(tokenizer, n_token_type=len(config.token_type), is_pretrain = False),
    shuffle=True,
    batch_size=config.batch_size,
)

val_dataloader = DataLoader(
    val_dataset,
    collate_fn=batcher(tokenizer, n_token_type=len(config.token_type), is_pretrain = False),
    shuffle=False,
    batch_size=config.batch_size,
)

test_dataloader = DataLoader(
    test_dataset,
    collate_fn=batcher(tokenizer, n_token_type=len(config.token_type), is_pretrain = False),
    shuffle=False,
    batch_size=config.batch_size,
)

In [13]:
for batch in train_dataloader:
    pass  # just to check if the dataloader works
for batch in val_dataloader:
    pass  # just to check if the dataloader works
for batch in test_dataloader:
    pass  # just to check if the dataloader works
print("All pass!")

All pass!


In [14]:
if curr_task in ["death", "stay", "readmission"]:
    eval_metric = "f1"
    task_type = "binary"
    loss_fn = F.binary_cross_entropy_with_logits
else:
    eval_metric = "f1"
    task_type = "l2r"
    loss_fn = lambda x, y: F.binary_cross_entropy_with_logits(x, y)

In [15]:
input_ids, token_types, adm_index, age_ids, diag_code_group_dicts, labels = next(iter(train_dataloader))
print("Input IDs shape:", input_ids.shape)
print("Token Types shape:", token_types.shape)
print("Admission Index shape:", adm_index.shape)
print("Age IDs shape:", age_ids.shape)
print("Diag Code Group Dict number:", len(diag_code_group_dicts))
print("Labels shape:", labels.shape)

Input IDs shape: torch.Size([32, 229])
Token Types shape: torch.Size([32, 229])
Admission Index shape: torch.Size([32, 229])
Age IDs shape: torch.Size([32, 5])
Diag Code Group Dict number: 32
Labels shape: torch.Size([32, 18])


# Model Walkthrough

In [16]:
# load pretrained model
if config.use_pretrained_model:
    pretrain_exp_name = (
    f"{config.dataset}-{config.pretrain_mask_rate}-{config.d_model}-{config.pretrain_cls_ontology_weight}-{config.pretrain_visit_ontology_weight}-{config.pretrain_adm_type_weight}"
)
    print(pretrain_exp_name)
    save_path = "./pretrained_models/" + pretrain_exp_name
    state_dict = torch.load(f"{save_path}/pretrained_model.pt", map_location="cpu")

MIMIC-III-0.7-64-0.05-0.05-0


In [17]:
final_metrics, final_long_seq_metrics = [], []
for i in range(15):
    print(f"================================{i+1}==================================")
    model = HeteroGTFineTune(tokenizer=tokenizer, token_types=config.token_type, d_model=config.d_model, num_heads=config.num_heads, layer_types=['gnn', 'tf', 'gnn', 'tf'], max_num_adms=config.max_num_adms, 
                     device=device, task=curr_task, label_vocab_size=config.label_vocab_size, attn_mask_dicts=config.attn_mask_dicts,
                     use_cls_cat=True).to(device)
    if config.use_pretrained_model:
        model.load_weight(state_dict)
    optimizer = torch.optim.AdamW(model.parameters(), lr=config.lr)
    best_test_metric, best_test_long_seq_metric = train_with_early_stopping(model, train_dataloader, val_dataloader, test_dataloader,
                                                                            optimizer, loss_fn, device, config.early_stop_patience, task_type, config.epochs, 
                                                                            dec_loss_lambda=config.dec_loss_lambda, 
                                                                            val_long_seq_idx=val_long_seq_idx, test_long_seq_idx=test_long_seq_idx, 
                                                                            eval_metric=eval_metric, return_model=False)
    final_metrics.append(best_test_metric)
    final_long_seq_metrics.append(best_test_long_seq_metric)

================================1==================================


Running inference: 100%|██████████| 36/36 [00:01<00:00, 22.89it/s]


                                           precision   recall       f1  \
Acute and unspecified renal failure          50.0000   5.4201   9.7800   
Acute cerebrovascular disease                 0.0000   0.0000   0.0000   
Acute myocardial infarction                   0.0000   0.0000   0.0000   
Cardiac dysrhythmias                         72.8324  26.5263  38.8889   
Chronic kidney disease                       70.5882   4.8980   9.1603   
Chronic obstructive pulmonary disease         0.0000   0.0000   0.0000   
Conduction disorders                          0.0000   0.0000   0.0000   
Congestive heart failure; nonhypertensive    78.8000  44.1704  56.6092   
Coronary atherosclerosis and related         73.3333   3.9286   7.4576   
Disorders of lipid metabolism                 0.0000   0.0000   0.0000   
Essential hypertension                       58.8235   9.3897  16.1943   
Fluid and electrolyte disorders              50.6024  18.3807  26.9663   
Gastrointestinal hemorrhage           

Running inference: 100%|██████████| 37/37 [00:01<00:00, 22.60it/s]


                                           precision   recall       f1  \
Acute and unspecified renal failure          63.1579   3.9474   7.4303   
Acute cerebrovascular disease                 0.0000   0.0000   0.0000   
Acute myocardial infarction                   0.0000   0.0000   0.0000   
Cardiac dysrhythmias                         69.4805  22.9614  34.5161   
Chronic kidney disease                       85.7143   4.4944   8.5409   
Chronic obstructive pulmonary disease         0.0000   0.0000   0.0000   
Conduction disorders                          0.0000   0.0000   0.0000   
Congestive heart failure; nonhypertensive    75.1152  36.8778  49.4689   
Coronary atherosclerosis and related        100.0000   2.4055   4.6980   
Disorders of lipid metabolism                 0.0000   0.0000   0.0000   
Essential hypertension                       53.8462   9.1146  15.5902   
Fluid and electrolyte disorders              52.7950  18.8889  27.8232   
Gastrointestinal hemorrhage           

...

                                           precision   recall       f1  \
Acute and unspecified renal failure          39.7770  35.1974  37.3473   
Acute cerebrovascular disease                 0.0000   0.0000   0.0000   
Acute myocardial infarction                  26.1905  14.8649  18.9655   
Cardiac dysrhythmias                         67.2727  63.5193  65.3422   
Chronic kidney disease                       68.7500  78.2772  73.2049   
Chronic obstructive pulmonary disease        54.9618  44.1718  48.9796   
Conduction disorders                          0.0000   0.0000   0.0000   
Congestive heart failure; nonhypertensive    64.8760  71.0407  67.8186   
Coronary atherosclerosis and related         60.0000  35.0515  44.2516   
Disorders of lipid metabolism                51.4451  57.7922  54.4343   
Essential hypertension                       58.4810  60.1562  59.3068   
Fluid and electrolyte disorders              47.7435  44.6667  46.1538   
Gastrointestinal hemorrhage           

Running inference: 100%|██████████| 36/36 [00:01<00:00, 22.27it/s]


                                           precision   recall       f1  \
Acute and unspecified renal failure          45.8015  48.7805  47.2441   
Acute cerebrovascular disease                15.0000  20.0000  17.1429   
Acute myocardial infarction                  28.5714   9.3023  14.0351   
Cardiac dysrhythmias                         72.5849  58.5263  64.8019   
Chronic kidney disease                       63.7066  67.3469  65.4762   
Chronic obstructive pulmonary disease        52.0408  32.6923  40.1575   
Conduction disorders                          0.0000   0.0000   0.0000   
Congestive heart failure; nonhypertensive    67.3378  67.4888  67.4132   
Coronary atherosclerosis and related         60.4255  50.7143  55.1456   
Disorders of lipid metabolism                55.1724  52.4590  53.7815   
Essential hypertension                       61.2293  60.7981  61.0130   
Fluid and electrolyte disorders              42.5110  42.2319  42.3710   
Gastrointestinal hemorrhage           

Running inference: 100%|██████████| 37/37 [00:01<00:00, 22.03it/s]


                                           precision   recall       f1  \
Acute and unspecified renal failure          41.6887  51.9737  46.2665   
Acute cerebrovascular disease                 5.0000   5.5556   5.2632   
Acute myocardial infarction                  32.0000  10.8108  16.1616   
Cardiac dysrhythmias                         71.7087  54.9356  62.2114   
Chronic kidney disease                       72.9630  73.7828  73.3706   
Chronic obstructive pulmonary disease        62.8866  37.4233  46.9231   
Conduction disorders                          0.0000   0.0000   0.0000   
Congestive heart failure; nonhypertensive    71.5347  65.3846  68.3215   
Coronary atherosclerosis and related         64.5455  48.7973  55.5773   
Disorders of lipid metabolism                55.3435  47.0779  50.8772   
Essential hypertension                       57.4257  60.4167  58.8832   
Fluid and electrolyte disorders              45.1247  44.2222  44.6689   
Gastrointestinal hemorrhage           

In [18]:
def topk_avg_performance_formatted(performances, long_seq_performances, k=5):
    metrics = ["f1", "auc", "prauc"]
    scores = {m: np.array([p[m] for p in performances]) for m in metrics}

    # 计算排名（值越大排名越靠前）
    ranks = {m: (-scores[m]).argsort().argsort() + 1 for m in metrics}
    avg_ranks = np.mean(np.stack([ranks[m] for m in metrics], axis=1), axis=1)

    # 选 top-k
    topk_idx = np.argsort(avg_ranks)[:k]
    final_avg = {m: np.mean([performances[i][m] for i in topk_idx]) for m in performances[0].keys()}
    final_std = {m: np.std([performances[i][m] for i in topk_idx], ddof=0) for m in performances[0].keys()}
    final_long_seq_avg = {m: np.mean([long_seq_performances[i][m] for i in topk_idx]) for m in long_seq_performances[0].keys()}
    final_long_seq_std = {m: np.std([long_seq_performances[i][m] for i in topk_idx], ddof=0) for m in long_seq_performances[0].keys()}

    # 打印结果（转百分比，均保留两位小数）
    print("Final Metrics:")
    for m in performances[0].keys():
        mean_val = final_avg[m]
        std_val = final_std[m]
        print(f"{m}: {mean_val:.2f} ± {std_val:.2f}")
    print("\nFinal Long Sequence Metrics:")
    for m in long_seq_performances[0].keys():
        mean_val = final_long_seq_avg[m]
        std_val = final_long_seq_std[m]
        print(f"{m}: {mean_val:.2f} ± {std_val:.2f}")

In [19]:
topk_avg_performance_formatted(final_metrics, final_long_seq_metrics)

Final Metrics:
precision: 41.94 ± 1.21
recall: 37.79 ± 1.51
f1: 38.64 ± 0.87
auc: 73.37 ± 0.60
prauc: 42.70 ± 0.43

Final Long Sequence Metrics:
precision: 42.06 ± 2.49
recall: 40.34 ± 2.45
f1: 40.05 ± 1.68
auc: 71.03 ± 1.25
prauc: 45.54 ± 0.45
